In [1]:
# Notebook parameters. Values here are for development only and 
# will be overridden when running via snakemake and papermill.
cohort_id = "CD-NU_Gbadolite_gamb_2015_Q3"
# cohort_id = 'ML-2_Kati_colu_2014_Q3'
# cohort_id = 'CI-LG_Agneby-Tiassa_colu_2012'
cohorts_analysis = "20230223"
contigs = ['2RL', '3RL', 'X']
sample_sets = "3.0"
min_cohort_size = 20
max_cohort_size = 50
h12_calibration_contig = '3L'
use_gcs_cache = False
dask_scheduler = "threads"

In [2]:
# Parameters
min_cohort_size = 20
max_cohort_size = 50
sample_sets = ["3.0"]
contigs = ["2RL", "3RL", "X"]
cohorts_analysis = "20230223"
h12_calibration_contig = "3L"
h12_signal_detection_min_delta_aic = 1000
h12_signal_detection_min_stat_max = 0.1
h12_signal_detection_gflanks = [6]
use_gcs_cache = False
dask_scheduler = "single-threaded"
cohort_id = "CF-BGF_Bangui_gamb_1994_Q1"


In [3]:
from IPython.display import Markdown, HTML
import malariagen_data
import numpy as np
import pandas as pd
from pyprojroot import here
import yaml
import dask
dask.config.set(scheduler=dask_scheduler);
from textwrap import dedent

import geopandas as gpd
import bokeh.layouts as bklay
import bokeh.plotting as bkplt
import bokeh.models as bkmod
import plotly.express as px

from bokeh.io import output_notebook # enables plot interface in J notebook

# N.B., do not add the "remove-output" tag to this cell!!! If you do,
# the bokeh javascript libraries will not get loaded in the generated
# HTML page. The call to output_notebook() injects javascript in the
# cell output which triggers the bokeh javascript libraries to be loaded
# in the page.
output_notebook(hide_banner=True)

# Central African Republic / Bangui / gambiae / 1994 / Q1

In [4]:
# Load cohorts to find sample query to select samples for this cohort.

df_cohorts = gpd.read_file(here() / "build" / "final_cohorts.geojson").set_index("cohort_id")
cohort = df_cohorts.loc[cohort_id]
cohort

cohort_size                                                          53
country                                        Central African Republic
admin1_iso                                                       CF-BGF
admin1_name                                                      Bangui
admin2_name                                                      Bangui
taxon                                                           gambiae
year                                                               1994
quarter                                                               1
cohort_label          Central African Republic / Bangui / gambiae / ...
sample_query          cohort_admin2_quarter == 'CF-BGF_Bangui_gamb_1...
latitude                                                          4.367
longitude                                                        18.583
h12_window_size                                                  1000.0
country_alpha2                                                  

In [5]:
# Initialise access to MalariaGEN data.

extra_params = dict()
if use_gcs_cache:
    extra_params["url"] = "simplecache::gs://vo_agam_release"
    extra_params["simplecache"] = dict(cache_storage=(here() / "gcs_cache").as_posix())

ag3 = malariagen_data.Ag3(
    # Pin the version of the cohorts analysis for reproducibility.
    cohorts_analysis=cohorts_analysis,
    results_cache=(here() / "malariagen_data_cache").as_posix(),
    **extra_params,
)
ag3

<MalariaGEN Ag3 API client>
Storage URL             : gs://vo_agam_release/
Data releases available : 3.0, 3.1, 3.2, 3.3, 3.4, 3.5, 3.6, 3.7, 3.8
Results cache           : /home/sanjaynagi/selection-atlas/malariagen_data_cache
Cohorts analysis        : 20230223
AIM analysis            : 20220528
Site filters analysis   : dt_20200416
Software version        : malariagen_data 7.13.0
Client location         : unknown
---
Please note that data are subject to terms of use,
for more information see https://www.malariagen.net/data
or contact data@malariagen.net. For API documentation see 
https://malariagen.github.io/vector-data/ag3/api.html

In [6]:
# Load sample metadata for this cohort.

df_samples = ag3.sample_metadata(sample_query=cohort['sample_query'])
df_samples

sample_id partner_sample_id             contributor  \
0    BK0009-C            RCA_10  Alessandra della Torre   
1    BK0010-C            RCA_11  Alessandra della Torre   
2    BK0011-C            RCA_12  Alessandra della Torre   
3    BK0013-C            RCA_14  Alessandra della Torre   
4    BK0016-C            RCA_17  Alessandra della Torre   
5    BK0018-C            RCA_20  Alessandra della Torre   
6    BK0019-C            RCA_21  Alessandra della Torre   
7    BK0022-C            RCA_25  Alessandra della Torre   
8    BK0023-C            RCA_27  Alessandra della Torre   
9    BK0026-C            RCA_32  Alessandra della Torre   
10   BK0027-C            RCA_33  Alessandra della Torre   
11   BK0029-C            RCA_35  Alessandra della Torre   
12   BK0030-C            RCA_36  Alessandra della Torre   
13   BK0032-C            RCA_38  Alessandra della Torre   
14   BK0033-C            RCA_39  Alessandra della Torre   
15   BK0034-C            RCA_40  Alessandra della Torre   
16   BK0037-C            RCA_43  Alessandra della Torre   
17   BK0038-C            RCA_44  Alessandra della Torre   
18   BK0039-C            RCA_45  Alessandra della Torre   
19   BK0040-C            RCA_46  Alessandra della Torre   
20   BK0043-C            RCA_50  Alessandra della Torre   
21   BK0045-C            RCA_52  Alessandra della Torre   
22   BK0046-C            RCA_53  Alessandra della Torre   
23   BK0047-C            RCA_54  Alessandra della Torre   
24   BK0048-C            RCA_55  Alessandra della Torre   
25   BK0049-C            RCA_56  Alessandra della Torre   
26   BK0050-C            RCA_57  Alessandra della Torre   
27   BK0051-C            RCA_58  Alessandra della Torre   
28   BK0053-C            RCA_60  Alessandra della Torre   
29   BK0054-C            RCA_61  Alessandra della Torre   
30   BK0055-C            RCA_62  Alessandra della Torre   
31   BK0056-C            RCA_63  Alessandra della Torre   
32   BK0057-C            RCA_64  Alessandra della Torre   
33   BK0058-C            RCA_65  Alessandra della Torre   
34   BK0059-C            RCA_66  Alessandra della Torre   
35   BK0061-C            RCA_68  Alessandra della Torre   
36   BK0062-C            RCA_69  Alessandra della Torre   
37   BK0063-C            RCA_70  Alessandra della Torre   
38   BK0064-C            RCA_71  Alessandra della Torre   
39   BK0066-C            RCA_73  Alessandra della Torre   
40   BK0069-C            RCA_76  Alessandra della Torre   
41   BK0070-C            RCA_77  Alessandra della Torre   
42   BK0071-C            RCA_78  Alessandra della Torre   
43   BK0072-C            RCA_79  Alessandra della Torre   
44   BK0074-C            RCA_81  Alessandra della Torre   
45   BK0077-C            RCA_84  Alessandra della Torre   
46   BK0078-C            RCA_85  Alessandra della Torre   
47   BK0080-C            RCA_88  Alessandra della Torre   
48   BK0082-C            RCA_90  Alessandra della Torre   
49   BK0083-C            RCA_91  Alessandra della Torre   
50   BK0085-C            RCA_93  Alessandra della Torre   
51   BK0086-C            RCA_94  Alessandra della Torre   
52  BK0094-CW           RCA_102  Alessandra della Torre   

                     country location  year  month  latitude  longitude  \
0   Central African Republic   Bangui  1994      1     4.367     18.583   
1   Central African Republic   Bangui  1994      1     4.367     18.583   
2   Central African Republic   Bangui  1994      1     4.367     18.583   
3   Central African Republic   Bangui  1994      1     4.367     18.583   
4   Central African Republic   Bangui  1994      1     4.367     18.583   
5   Central African Republic   Bangui  1994      1     4.367     18.583   
6   Central African Republic   Bangui  1994      1     4.367     18.583   
7   Central African Republic   Bangui  1994      1     4.367     18.583   
8   Central African Republic   Bangui  1994      1     4.367     18.583   
9   Central African Republic   Bangui  1994      1     4.367     18

In [7]:
# Determine collection dates.

df_collection_dates = (
    df_samples
    .groupby(["year", "month"])
    .size()
    .reset_index()
    .rename(columns={0: 'count'})
)
df_collection_dates

year  month  count
0  1994      1     53

In [8]:
# Determine first and last collection months.

min_month = df_collection_dates["month"].min()
max_month = df_collection_dates["month"].max()

if min_month < 0:
    start_month = end_month = None
else:
    start_month = pd.to_datetime(min_month, format="%m").month_name()
    end_month = pd.to_datetime(max_month, format="%m").month_name()
    
start_month, end_month

('January', 'January')

In [9]:
# Determine unique collection locations.

df_locations = df_samples[["location", "longitude", "latitude"]].drop_duplicates()
df_locations

location  longitude  latitude
0   Bangui     18.583     4.367

In [10]:
# Extract provenance information about the samples.

df_contributors = df_samples[["release", "sample_set", "contributor"]].drop_duplicates()
df_contributors["study"] = df_contributors.apply(
    lambda v: "Ag1000G" if v["sample_set"].startswith("AG1000G") else "TODO",
    axis="columns"
)
df_contributors["release"] = df_contributors["release"].apply(
    lambda v: f"Ag{v}"
)
df_contributors.rename(columns={
    "contributor": "Contributor",
    "study": "Study",
    "release": "Data release",
    "sample_set": "Sample set",
}, inplace=True)
df_contributors.set_index(["Contributor", "Study", "Data release"], inplace=True)
df_contributors

Sample set
Contributor            Study   Data release            
Alessandra della Torre Ag1000G Ag3.0         AG1000G-CF

In [11]:
# Build a paragraph with summary information about the samples in this cohort.

n_locations = len(df_locations)

summary_info = f"""This cohort comprises {cohort['cohort_size']:,} samples from the 
*{cohort['taxon']}* taxon, collected from {n_locations} locations within the administrative 
division of {cohort['admin2_name']}, {cohort['admin1_name']}, {cohort['country']}."""

if start_month and start_month == end_month:
    summary_info += f""" Collections were made in {start_month} {cohort['year']}."""
elif start_month:
    summary_info += f""" Collections were made between {start_month} and {end_month} in {cohort['year']}."""
else:
    summary_info += f""" Collections were made in {cohort['year']}."""
    
display(Markdown(summary_info))


This cohort comprises 53 samples from the 
*gambiae* taxon, collected from 1 locations within the administrative 
division of Bangui, Bangui, Central African Republic. Collections were made in January 1994.

## Selection scans

In [12]:
# load signals to overlay on H12 plots
import pandas as pd

df_signals_contigs = []
for contig in contigs:

    try:
        df_signals_contig = pd.read_csv(here() / "build/h12-signal-detection/" / f"{cohort_id}_{contig}.csv")
    except pd.errors.EmptyDataError:
        df_signals_contig = pd.DataFrame()
    df_signals_contigs.append(df_signals_contig)  
    
df_signals = pd.concat(df_signals_contigs)

# Add extra columns to help with overlaying signals on plots.
df_signals["bottom"] = 0
df_signals["top"] = 1

df_signals

cohort_id contig     gcenter   pcenter  delta_i  stat_max  \
0  CF-BGF_Bangui_gamb_1994_Q1    2RL  119.879733  62827600     1460    0.3830   
1  CF-BGF_Bangui_gamb_1994_Q1    2RL  166.451420  86996342     5743    0.5356   
0  CF-BGF_Bangui_gamb_1994_Q1    3RL   57.165296  28582648     4376    0.2090   
1  CF-BGF_Bangui_gamb_1994_Q1    3RL  130.876686  67620999     1191    0.1536   

     gpos_max  ppos_max  focus_gstart  focus_gstop  ...      skew  decay_left  \
0  119.897354  62862842    119.570709   120.212432  ... -0.053251    1.236094   
1  166.393256  86967259    166.288086   166.635829  ... -0.087540    0.653336   
0   57.119268  28559634     57.013078    57.284518  ...  0.176244    0.608870   
1  130.889733  67627522    130.856509   130.907662  ... -0.309245    0.080706   

   decay_right  baseline           aic           bic       rss  constant_aic  \
0     1.330797  0.030122 -10491.677848 -10464.886879  1.944420  -9031.288350   
1     0.737634  0.037308 -15351.287608 -15323.389214  0.766655  -9607.388153   
0     0.476887  0.018031 -17936.545563 -17908.903904  0.119990 -13559.863717   
1     0.123906  0.018952 -17141.798255 -17114.498682  0.089415 -15949.829017   

   bottom  top  
0       0    1  
1       0    1  
0       0    1  
1       0    1  

[4 rows x 32 columns]

In [13]:
# load window sizes 
h12_calibration_dir = "build/h12-calibration"
with open(here() / h12_calibration_dir / f"{cohort_id}.yaml") as h12_calibration_file:
    h12_calibration_params = yaml.safe_load(h12_calibration_file)
h12_window_size = h12_calibration_params["h12_window_size"]
g123_calibration_dir = "build/g123-calibration"
with open(here() / g123_calibration_dir / f"{cohort_id}.yaml") as g123_calibration_file:
    g123_calibration_params = yaml.safe_load(g123_calibration_file)
g123_window_size = g123_calibration_params["g123_window_size"]

if cohort.taxon == 'arabiensis':
    phasing_analysis = 'arab'
else:
    phasing_analysis = 'gamb_colu'

ihs_window_size = 100

def plot_h12_g123_ihs_tracks(
        contig, 
        df_signals,
        sizing_mode='stretch_width', 
        show=False, 
        width=800, 
        track_height=150,
        genes_height=90,
    ):

    sample_query = cohort["sample_query"]
    
    fig1 = ag3.plot_h12_gwss_track(
        contig=contig, 
        window_size=h12_window_size, 
        analysis=phasing_analysis, 
        sample_sets=sample_sets,
        sample_query=sample_query, 
        min_cohort_size=min_cohort_size,
        max_cohort_size=max_cohort_size,
        sizing_mode=sizing_mode,
        show=show,
        width=width,
        height=track_height,
    )
    fig1.xaxis.visible = False
        
    if not df_signals.empty:
        df = df_signals.query("contig == @contig")
        center_xs = [np.array([row.pcenter, row.pcenter]) for idx, row in df.iterrows()]
        center_ys = [np.array([0, 1]) for idx, row in df.iterrows()]
        source = bkmod.ColumnDataSource(data={
            'cohort': df.cohort_id,
            'chromosome': df.contig,
            'score': df.delta_i.astype(int),
            'peak_start': df.span2_pstart,
            'peak_stop': df.span2_pstop,
            'focus_start': df.focus_pstart,
            'focus_stop': df.focus_pstop,    
            'center_xs': center_xs,
            'center_ys': center_ys,
            'bottom': df.bottom ,
            'top': df.top,
            })
        quad = fig1.quad(bottom='bottom', top='top', left='peak_start', right='peak_stop', 
              source=source, color="gray", alpha=.1, line_width=1)
        quad2 = fig1.quad(bottom='bottom', top='top', left='focus_start', right='focus_stop', 
              source=source, color="red", alpha=.4)
        glyph = bkmod.MultiLine(xs='center_xs', ys='center_ys', line_color='red', line_width=2, line_alpha=0.8)
        fig1.add_glyph(source, glyph)
    
        hover = bkmod.HoverTool(tooltips=[
            ("Cohort", '@cohort'),
            ("Score", '@score'),
            ("Focus", "@focus_start{,} - @focus_stop{,}"),
        ], renderers=[quad])

        fig1.add_tools(hover)
    
    fig2 = ag3.plot_g123_gwss_track(
        contig=contig, 
        window_size=g123_window_size, 
        sites=phasing_analysis,
        site_mask=phasing_analysis, 
        sample_sets=sample_sets,
        sample_query=sample_query, 
        min_cohort_size=min_cohort_size,
        max_cohort_size=max_cohort_size,
        sizing_mode=sizing_mode,
        width=width,
        height=track_height,
        show=show,
        title="",
        x_range=fig1.x_range,
    )
    fig2.xaxis.visible = False

    fig3 = ag3.plot_ihs_gwss_track(
        contig=contig, 
        window_size=ihs_window_size, 
        analysis=phasing_analysis, 
        sample_sets=sample_sets,
        sample_query=sample_query, 
        min_cohort_size=min_cohort_size,
        max_cohort_size=max_cohort_size,
        sizing_mode=sizing_mode,
        width=width,
        height=track_height,
        show=show,
        title="",
        x_range=fig1.x_range,
    )
    fig3.xaxis.visible = False


    fig4 = ag3.plot_genes(
        region=contig, 
        show=show,
        sizing_mode=sizing_mode,
        width=width,
        height=genes_height,
        x_range=fig1.x_range
        )
                        
    fig = bklay.gridplot(
        [fig1, fig2, fig3, fig4],
        ncols=1,
        toolbar_location="above",
        merge_tools=True,
        sizing_mode=sizing_mode,
    )
    return fig 

In [14]:
for contig in contigs:
    
    display(HTML(f"<h3>Chromosome {contig}</h3>"))
    
    fig = plot_h12_g123_ihs_tracks(
        contig=contig,
        df_signals=df_signals,
    );

    bkplt.show(fig)


## Sampling information

In [15]:
from ipyleaflet import Map, Marker, basemaps
from ipywidgets import HTML

center = cohort[['latitude', 'longitude']].to_list()
m = Map(center=center, zoom=9, basemap=basemaps.OpenTopoMap)

df = df_samples[['latitude', 'longitude', 'taxon']].groupby(['latitude', 'longitude', 'taxon']).size().to_frame().rename(columns={0: 'count'}).reset_index()

for coh_id, row in df.iterrows():
    lat, long = row[['latitude', 'longitude']]
    
    if row['taxon'] == 'gambiae':
        color= 'red'
    elif row['taxon'] == 'coluzzii':
        color='cadetblue'
    elif row['taxon'] == 'arabiensis':
        color='lightgreen'
    else: 
        color='gray'

    marker = Marker(location=(lat, long), draggable=False, opacity=0.7, color=color)
    m.add_layer(marker);

    message2 = HTML()
    message2.value = f"n = {row['count']}"
    marker.popup = message2

display(m)

Map(center=[4.367, 18.583], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title', 'zoom_…

In [16]:

if min_month >= 0:
    # For this cohort we have month data, so show a breakdown of sample
    # numbers by location and month.
    
    # Construct a pivot table counting samples.
    df_loc_dt = df_samples.pivot_table(
        index=["location", "longitude", "latitude"],
        columns="month",
        values="sample_id",
        aggfunc="count",
        fill_value=0,
    )

    # Tidy up the columns using a multi index.
    df_loc_dt.reset_index(inplace=True)
    cols = pd.MultiIndex.from_tuples(
        [("Location", "Name"), ("Location", "Longitude"), ("Location", "Latitude")] + 
        [("Date", pd.to_datetime(x, format="%m").month_name()) 
         for x in df_loc_dt.columns[3:]], 
    )
    df_loc_dt.columns = cols
    
else:
    # For this cohort we do not have month data, so show a breakdown of sample
    # numbers by location only.
    
    # Construct a pivot table counting samples.
    df_loc_dt = df_samples.groupby(["location", "longitude", "latitude"]).agg({"sample_id": "count"})

    # Tidy up the columns using a multi index.
    df_loc_dt.reset_index(inplace=True)
    cols = pd.MultiIndex.from_tuples(
        [("Location", "Name"), ("Location", "Longitude"), ("Location", "Latitude"), ("Date", cohort.year)]
    )
    df_loc_dt.columns = cols

# Style the table.
df_loc_dt_styled = (
    df_loc_dt
    .style
    .format(precision=3)
    .set_caption("Number of samples collected.")
    .hide()
)
display(df_loc_dt_styled)    

## Diagnostics
### H12 calibration

In [17]:
display(Markdown(f"Selected window size: **{h12_window_size:,}**"))

window_sizes = (100, 200, 500, 1000, 2000, 5000, 10000, 20000)

ag3.plot_h12_calibration(
    contig=h12_calibration_contig,
    analysis=phasing_analysis,
    sample_sets=sample_sets,
    sample_query=cohort['sample_query'],
    min_cohort_size=min_cohort_size,
    max_cohort_size=max_cohort_size,
    window_sizes=window_sizes,
);


Selected window size: **1,000**

### G123 Calibration

In [18]:
display(Markdown(f"Selected window size: **{g123_window_size:,}**"))

ag3.plot_g123_calibration(
    contig=h12_calibration_contig,
    sites=phasing_analysis,
    site_mask=phasing_analysis,
    sample_sets=sample_sets,
    sample_query=cohort['sample_query'],
    min_cohort_size=min_cohort_size,
    max_cohort_size=max_cohort_size,
    window_sizes=window_sizes,
);

Selected window size: **500**

## Data sources

In [19]:
df_sources_style = (
    df_contributors
    .style
    .set_caption("MalariaGEN Vector Observatory partners, studies and sample sets contributing data for this cohort.")
)
df_sources_style